# MSD 歌曲推荐——数据预处理
1. 计算每个用户的总播放次数，找出播放次数最多的用户（最活跃的前800个用户）
2. 计算每首歌曲的总播放次数，找出播放次数最多的歌曲（最流行的前800首歌曲）
3. 从总数据集中抽取最活跃的前800个用户、最流行的前800首歌曲的播放记录

In [1]:
#coding=utf-8

In [2]:
import pandas as pd
import numpy as np
import time

#Python SQLITE数据库是一款非常小巧的嵌入式开源数据库软件
import sqlite3

## 载入原始数据

### Get more information about the Millionsong project from https://labrosa.ee.columbia.edu/millionsong/

### Load Triplets data  [user, song, play_count]
#### Get the data from http://labrosa.ee.columbia.edu/millionsong/sites/default/files/challenge/train_triplets.txt.zip

In [24]:
#数据集太大，读10000条记录看看
dpath = './data/'
df_triplet_dataset = pd.read_csv(filepath_or_buffer = dpath + 'train_triplets.txt', 
                              nrows=10000,sep='\t', header=None, 
                              names=['user','song','play_count'])

In [25]:
df_triplet_dataset.head(n=20)

user                song  play_count
0   4e11f45d732f4861772b2906f81a7d384552ad12  SOCKSGZ12A58A7CA4B           1
1   4e11f45d732f4861772b2906f81a7d384552ad12  SOCVTLJ12A6310F0FD           1
2   4e11f45d732f4861772b2906f81a7d384552ad12  SODLLYS12A8C13A96B           3
3   4e11f45d732f4861772b2906f81a7d384552ad12  SOEGIYH12A6D4FC0E3           1
4   4e11f45d732f4861772b2906f81a7d384552ad12  SOFRQTD12A81C233C0           2
5   4e11f45d732f4861772b2906f81a7d384552ad12  SOHEMBB12A6701E907           1
6   4e11f45d732f4861772b2906f81a7d384552ad12  SOHJOLH12A6310DFE5           1
7   4e11f45d732f4861772b2906f81a7d384552ad12  SOIZLKI12A6D4F7B61           1
8   4e11f45d732f4861772b2906f81a7d384552ad12  SOJGSIO12A8C141DBF           1
9   4e11f45d732f4861772b2906f81a7d384552ad12  SOKEYJQ12A6D4F6132           1
10  4e11f45d732f4861772b2906f81a7d384552ad12  SOKLRPJ12A8C13C3FE           1
11  4e11f45d732f4861772b2906f81a7d384552ad12  SOKNWRZ12A8C13BF62           2
12  4e11f45d732f4861772b2906f81a7d384552ad12  SOKXYUW12A8C140229           1
13  4e11f45d732f4861772b2906f81a7d384552ad12  SOLAUOW12A8C13A400           3
14  4e11f45d732f4861772b2906f81a7d384552ad12  SOLLDVS12AB0183835           6
15  4e11f45d732f4861772b2906f81a7d384552ad12  SOLOZRE12A8C133256           1
16  4e11f45d732f4861772b2906f81a7d384552ad12  SOLWRZI12A6D4FC4F0           1
17  4e11f45d732f4861772b2906f81a7d384552ad12  SOMDVSL12A6D4F7230           2
18  4e11f45d732f4861772b2906f81a7d384552ad12  SOMGIYR12AB0187973           1
19  4e11f45d732f4861772b2906f81a7d384552ad12  SOMNGMO12A6702187E           1

## 计算每个用户的总播放次数 和每首歌曲的播放次数
看哪些用户最活跃（play counts最多）
由于空间有限，不活跃的用户不考虑了（共有约1M用户）
不流行的歌曲也不考虑了

In [40]:
output_dict_users = {} #user及对应的play_count次数集合(在所有的歌曲上求和)
output_dict_songs = {} #song及对应的play_count次数集合(在所有的歌曲上求和)

#也可以用read_csv
with open(dpath + 'train_triplets.txt') as f:
    for line_number, line in enumerate(f):
        cols = line.strip().split("\t")
        user = cols[0]            #第一列为用户id
        song = cols[1]            #第二列为歌曲id
        play_count = int(cols[2]) #第三列为播放次数
        
        if user in output_dict_users:
            play_count += output_dict_users[user]
        output_dict_users.update({user:play_count})
        
        if song in output_dict_songs:
            play_count += output_dict_songs[song]
        output_dict_songs.update({song:play_count})

#用户——播放次数列表
output_list_users = [{'user':k,'play_count':v} for k,v in output_dict_users.items()]
df_users_play_count = pd.DataFrame(output_list_users)

#按总播放次数排序
df_users_play_count = df_users_play_count.sort_values(by = 'play_count', ascending = False)
df_users_play_count.to_csv(path_or_buf= dpath + 'users_playcount.csv', index = False)


#歌曲——播放次数列表
output_list_songs = [{'song':k,'play_count':v} for k,v in output_dict_songs.items()]
df_songs_play_count = pd.DataFrame(output_list_songs)

#按总播放次数排序
df_songs_play_count = df_songs_play_count.sort_values(by = 'play_count', ascending = False)
df_songs_play_count.to_csv(path_or_buf= dpath + 'songs_playcount.csv', index = False)

['4e11f45d732f4861772b2906f81a7d384552ad12', 'SOCKSGZ12A58A7CA4B', '1']
4e11f45d732f4861772b2906f81a7d384552ad12
SOCKSGZ12A58A7CA4B
1
['4e11f45d732f4861772b2906f81a7d384552ad12', 'SOCVTLJ12A6310F0FD', '1']
4e11f45d732f4861772b2906f81a7d384552ad12
SOCVTLJ12A6310F0FD
1
['4e11f45d732f4861772b2906f81a7d384552ad12', 'SODLLYS12A8C13A96B', '3']
4e11f45d732f4861772b2906f81a7d384552ad12
SODLLYS12A8C13A96B
3
['4e11f45d732f4861772b2906f81a7d384552ad12', 'SOEGIYH12A6D4FC0E3', '1']
4e11f45d732f4861772b2906f81a7d384552ad12
SOEGIYH12A6D4FC0E3
1
['4e11f45d732f4861772b2906f81a7d384552ad12', 'SOFRQTD12A81C233C0', '2']
4e11f45d732f4861772b2906f81a7d384552ad12
SOFRQTD12A81C233C0
2
['4e11f45d732f4861772b2906f81a7d384552ad12', 'SOHEMBB12A6701E907', '1']
4e11f45d732f4861772b2906f81a7d384552ad12
SOHEMBB12A6701E907
1
['4e11f45d732f4861772b2906f81a7d384552ad12', 'SOHJOLH12A6310DFE5', '1']
4e11f45d732f4861772b2906f81a7d384552ad12
SOHJOLH12A6310DFE5
1
['4e11f45d732f4861772b2906f81a7d384552ad12', 'SOIZLKI12A6D4F7B

SOGTQNI12AB0184A5C
2
['67874d1a189c83326c529e554be6f7acf55effae', 'SOHTKMO12AB01843B0', '5']
67874d1a189c83326c529e554be6f7acf55effae
SOHTKMO12AB01843B0
5
['67874d1a189c83326c529e554be6f7acf55effae', 'SOIIOUS12A8AE47E20', '7']
67874d1a189c83326c529e554be6f7acf55effae
SOIIOUS12A8AE47E20
7
['67874d1a189c83326c529e554be6f7acf55effae', 'SOIZAZL12A6701C53B', '6']
67874d1a189c83326c529e554be6f7acf55effae
SOIZAZL12A6701C53B
6
['67874d1a189c83326c529e554be6f7acf55effae', 'SOKMHKY12AF72AB079', '4']
67874d1a189c83326c529e554be6f7acf55effae
SOKMHKY12AF72AB079
4
['67874d1a189c83326c529e554be6f7acf55effae', 'SOKUPAO12AB018D576', '2']
67874d1a189c83326c529e554be6f7acf55effae
SOKUPAO12AB018D576
2
['67874d1a189c83326c529e554be6f7acf55effae', 'SOKZZGT12A67ADA4C3', '6']
67874d1a189c83326c529e554be6f7acf55effae
SOKZZGT12A67ADA4C3
6
['67874d1a189c83326c529e554be6f7acf55effae', 'SOLFXKT12AB017E3E0', '8']
67874d1a189c83326c529e554be6f7acf55effae
SOLFXKT12AB017E3E0
8
['67874d1a189c83326c529e554be6f7acf55effa

9c859962257112ad523f1d3c121d35191daa6d2b
SONQJCU12A8C144398
4
['9c859962257112ad523f1d3c121d35191daa6d2b', 'SONWUZV12AB0180BAD', '21']
9c859962257112ad523f1d3c121d35191daa6d2b
SONWUZV12AB0180BAD
21
['9c859962257112ad523f1d3c121d35191daa6d2b', 'SOOBGSW12A6D4F9D51', '6']
9c859962257112ad523f1d3c121d35191daa6d2b
SOOBGSW12A6D4F9D51
6
['9c859962257112ad523f1d3c121d35191daa6d2b', 'SOODHLO12AF72A1980', '1']
9c859962257112ad523f1d3c121d35191daa6d2b
SOODHLO12AF72A1980
1
['9c859962257112ad523f1d3c121d35191daa6d2b', 'SOOTKWZ12AB0181082', '3']
9c859962257112ad523f1d3c121d35191daa6d2b
SOOTKWZ12AB0181082
3
['9c859962257112ad523f1d3c121d35191daa6d2b', 'SOOWPBJ12A8C137FB4', '1']
9c859962257112ad523f1d3c121d35191daa6d2b
SOOWPBJ12A8C137FB4
1
['9c859962257112ad523f1d3c121d35191daa6d2b', 'SOOWVNN12A8C140775', '1']
9c859962257112ad523f1d3c121d35191daa6d2b
SOOWVNN12A8C140775
1
['9c859962257112ad523f1d3c121d35191daa6d2b', 'SOOXLND12A6D4FE36E', '2']
9c859962257112ad523f1d3c121d35191daa6d2b
SOOXLND12A6D4FE36E


0b19fe0fad7ca85693846f7dad047c449784647e
SOJKQSF12A6D4F5EE9
1
['0b19fe0fad7ca85693846f7dad047c449784647e', 'SOJSTYO12A8C13F200', '5']
0b19fe0fad7ca85693846f7dad047c449784647e
SOJSTYO12A8C13F200
5
['0b19fe0fad7ca85693846f7dad047c449784647e', 'SOJTLHS12A8C13F633', '5']
0b19fe0fad7ca85693846f7dad047c449784647e
SOJTLHS12A8C13F633
5
['0b19fe0fad7ca85693846f7dad047c449784647e', 'SOJYBJZ12AB01801D0', '1']
0b19fe0fad7ca85693846f7dad047c449784647e
SOJYBJZ12AB01801D0
1
['0b19fe0fad7ca85693846f7dad047c449784647e', 'SOKLRPJ12A8C13C3FE', '4']
0b19fe0fad7ca85693846f7dad047c449784647e
SOKLRPJ12A8C13C3FE
4
['0b19fe0fad7ca85693846f7dad047c449784647e', 'SOKMHKY12AF72AB079', '3']
0b19fe0fad7ca85693846f7dad047c449784647e
SOKMHKY12AF72AB079
3
['0b19fe0fad7ca85693846f7dad047c449784647e', 'SOKOXWU12AF72AD1BC', '4']
0b19fe0fad7ca85693846f7dad047c449784647e
SOKOXWU12AF72AD1BC
4
['0b19fe0fad7ca85693846f7dad047c449784647e', 'SOKRAMY12A8C140804', '1']
0b19fe0fad7ca85693846f7dad047c449784647e
SOKRAMY12A8C140804
1


['4be305e02f4e72dad1b8ac78e630403543bab994', 'SOIIOUS12A8AE47E20', '3']
4be305e02f4e72dad1b8ac78e630403543bab994
SOIIOUS12A8AE47E20
3
['4be305e02f4e72dad1b8ac78e630403543bab994', 'SOISNSU12AC468C0D8', '113']
4be305e02f4e72dad1b8ac78e630403543bab994
SOISNSU12AC468C0D8
113
['4be305e02f4e72dad1b8ac78e630403543bab994', 'SOIZFTE12AB0186842', '24']
4be305e02f4e72dad1b8ac78e630403543bab994
SOIZFTE12AB0186842
24
['4be305e02f4e72dad1b8ac78e630403543bab994', 'SOIZLKI12A6D4F7B61', '101']
4be305e02f4e72dad1b8ac78e630403543bab994
SOIZLKI12A6D4F7B61
101
['4be305e02f4e72dad1b8ac78e630403543bab994', 'SOJGZXL12A6D4F2980', '1']
4be305e02f4e72dad1b8ac78e630403543bab994
SOJGZXL12A6D4F2980
1
['4be305e02f4e72dad1b8ac78e630403543bab994', 'SOJSTYO12A8C13F200', '1']
4be305e02f4e72dad1b8ac78e630403543bab994
SOJSTYO12A8C13F200
1
['4be305e02f4e72dad1b8ac78e630403543bab994', 'SOJTLHS12A8C13F633', '7']
4be305e02f4e72dad1b8ac78e630403543bab994
SOJTLHS12A8C13F633
7
['4be305e02f4e72dad1b8ac78e630403543bab994', 'SOJYBJ

...

3ab78e39bddeaeb789edad041fff03050077417c
SOOYDAZ12A58A7AE08
9
['13a2d690b099bcd3fdd256bd39aa14edadd5db08', 'SOAUWYT12A81C206F1', '45']
13a2d690b099bcd3fdd256bd39aa14edadd5db08
SOAUWYT12A81C206F1
45
['13a2d690b099bcd3fdd256bd39aa14edadd5db08', 'SOAXGDH12A8C13F8A1', '14']
13a2d690b099bcd3fdd256bd39aa14edadd5db08
SOAXGDH12A8C13F8A1
14
['13a2d690b099bcd3fdd256bd39aa14edadd5db08', 'SOBONKR12A58A7A7E0', '6']
13a2d690b099bcd3fdd256bd39aa14edadd5db08
SOBONKR12A58A7A7E0
6
['13a2d690b099bcd3fdd256bd39aa14edadd5db08', 'SOBOUPA12A6D4F81F1', '1']
13a2d690b099bcd3fdd256bd39aa14edadd5db08
SOBOUPA12A6D4F81F1
1
['13a2d690b099bcd3fdd256bd39aa14edadd5db08', 'SOCKSGZ12A58A7CA4B', '2']
13a2d690b099bcd3fdd256bd39aa14edadd5db08
SOCKSGZ12A58A7CA4B
2
['13a2d690b099bcd3fdd256bd39aa14edadd5db08', 'SOCVTLJ12A6310F0FD', '3']
13a2d690b099bcd3fdd256bd39aa14edadd5db08
SOCVTLJ12A6310F0FD
3
['13a2d690b099bcd3fdd256bd39aa14edadd5db08', 'SODGJKH12AAA8C9487', '8']
13a2d690b099bcd3fdd256bd39aa14edadd5db08
SODGJKH12AAA8C948

['a05e548059abb1f77cad6cb9c3c0c48e0616f551', 'SOPSOHT12A67AE0235', '1']
a05e548059abb1f77cad6cb9c3c0c48e0616f551
SOPSOHT12A67AE0235
1
['a05e548059abb1f77cad6cb9c3c0c48e0616f551', 'SOPUCYA12A8C13A694', '1']
a05e548059abb1f77cad6cb9c3c0c48e0616f551
SOPUCYA12A8C13A694
1
['a05e548059abb1f77cad6cb9c3c0c48e0616f551', 'SOPVQLJ12A67AE2281', '1']
a05e548059abb1f77cad6cb9c3c0c48e0616f551
SOPVQLJ12A67AE2281
1
['a05e548059abb1f77cad6cb9c3c0c48e0616f551', 'SOQCGHN12AB0181246', '1']
a05e548059abb1f77cad6cb9c3c0c48e0616f551
SOQCGHN12AB0181246
1
['a05e548059abb1f77cad6cb9c3c0c48e0616f551', 'SOQGSUC12A8C13B66D', '1']
a05e548059abb1f77cad6cb9c3c0c48e0616f551
SOQGSUC12A8C13B66D
1
['a05e548059abb1f77cad6cb9c3c0c48e0616f551', 'SOQJLWB12A6701E7B3', '1']
a05e548059abb1f77cad6cb9c3c0c48e0616f551
SOQJLWB12A6701E7B3
1
['a05e548059abb1f77cad6cb9c3c0c48e0616f551', 'SOQLFRX12A6D4F9200', '1']
a05e548059abb1f77cad6cb9c3c0c48e0616f551
SOQLFRX12A6D4F9200
1
['a05e548059abb1f77cad6cb9c3c0c48e0616f551', 'SOQZYQH12A8AE468

['d0a2c5ac5ce1bc3573224d910fe3adfb85d4ee3f', 'SOWCKVR12A8C142411', '1']
d0a2c5ac5ce1bc3573224d910fe3adfb85d4ee3f
SOWCKVR12A8C142411
1
['d0a2c5ac5ce1bc3573224d910fe3adfb85d4ee3f', 'SOWFIFP12A8C13A9EE', '1']
d0a2c5ac5ce1bc3573224d910fe3adfb85d4ee3f
SOWFIFP12A8C13A9EE
1
['d0a2c5ac5ce1bc3573224d910fe3adfb85d4ee3f', 'SOWSPUS12AC468BEE3', '11']
d0a2c5ac5ce1bc3573224d910fe3adfb85d4ee3f
SOWSPUS12AC468BEE3
11
['d0a2c5ac5ce1bc3573224d910fe3adfb85d4ee3f', 'SOXFXDH12A8C13326E', '17']
d0a2c5ac5ce1bc3573224d910fe3adfb85d4ee3f
SOXFXDH12A8C13326E
17
['d0a2c5ac5ce1bc3573224d910fe3adfb85d4ee3f', 'SOXLDLO12AB0186373', '23']
d0a2c5ac5ce1bc3573224d910fe3adfb85d4ee3f
SOXLDLO12AB0186373
23
['d0a2c5ac5ce1bc3573224d910fe3adfb85d4ee3f', 'SOXPFLM12A8AE48C50', '6']
d0a2c5ac5ce1bc3573224d910fe3adfb85d4ee3f
SOXPFLM12A8AE48C50
6
['d0a2c5ac5ce1bc3573224d910fe3adfb85d4ee3f', 'SOYGQGR12AF72ABAB8', '2']
d0a2c5ac5ce1bc3573224d910fe3adfb85d4ee3f
SOYGQGR12AF72ABAB8
2
['d0a2c5ac5ce1bc3573224d910fe3adfb85d4ee3f', 'SOZVCRW12A

12
['8ec7fd0c1acf1dbe44720e5eab44dbe524eb6caf', 'SOSZJFV12AB01878CB', '19']
8ec7fd0c1acf1dbe44720e5eab44dbe524eb6caf
SOSZJFV12AB01878CB
19
['8ec7fd0c1acf1dbe44720e5eab44dbe524eb6caf', 'SOTCMDJ12A6D4F8528', '8']
8ec7fd0c1acf1dbe44720e5eab44dbe524eb6caf
SOTCMDJ12A6D4F8528
8
['8ec7fd0c1acf1dbe44720e5eab44dbe524eb6caf', 'SOTEGWG12AB01897AC', '9']
8ec7fd0c1acf1dbe44720e5eab44dbe524eb6caf
SOTEGWG12AB01897AC
9
['8ec7fd0c1acf1dbe44720e5eab44dbe524eb6caf', 'SOTEKMT12A67AD954E', '1']
8ec7fd0c1acf1dbe44720e5eab44dbe524eb6caf
SOTEKMT12A67AD954E
1
['8ec7fd0c1acf1dbe44720e5eab44dbe524eb6caf', 'SOTHABI12A58A7DACB', '1']
8ec7fd0c1acf1dbe44720e5eab44dbe524eb6caf
SOTHABI12A58A7DACB
1
['8ec7fd0c1acf1dbe44720e5eab44dbe524eb6caf', 'SOTNHIP12AB0183131', '1']
8ec7fd0c1acf1dbe44720e5eab44dbe524eb6caf
SOTNHIP12AB0183131
1
['8ec7fd0c1acf1dbe44720e5eab44dbe524eb6caf', 'SOTUCYL12A8C14487F', '1']
8ec7fd0c1acf1dbe44720e5eab44dbe524eb6caf
SOTUCYL12A8C14487F
1
['8ec7fd0c1acf1dbe44720e5eab44dbe524eb6caf', 'SOTVMLE12AB

3
['6c6289326f70321f2b3e072daa44819efc55639a', 'SOOLULU12A6701FBC4', '4']
6c6289326f70321f2b3e072daa44819efc55639a
SOOLULU12A6701FBC4
4
['6c6289326f70321f2b3e072daa44819efc55639a', 'SOOWVNN12A8C140775', '2']
6c6289326f70321f2b3e072daa44819efc55639a
SOOWVNN12A8C140775
2
['6c6289326f70321f2b3e072daa44819efc55639a', 'SOOYDAZ12A58A7AE08', '3']
6c6289326f70321f2b3e072daa44819efc55639a
SOOYDAZ12A58A7AE08
3
['6c6289326f70321f2b3e072daa44819efc55639a', 'SOPAYPV12AB017DB0C', '7']
6c6289326f70321f2b3e072daa44819efc55639a
SOPAYPV12AB017DB0C
7
['6c6289326f70321f2b3e072daa44819efc55639a', 'SOPCTBB12AF72A1B64', '3']
6c6289326f70321f2b3e072daa44819efc55639a
SOPCTBB12AF72A1B64
3
['6c6289326f70321f2b3e072daa44819efc55639a', 'SOPPROJ12AB0184E18', '5']
6c6289326f70321f2b3e072daa44819efc55639a
SOPPROJ12AB0184E18
5
['6c6289326f70321f2b3e072daa44819efc55639a', 'SOPQLBY12A6310E992', '5']
6c6289326f70321f2b3e072daa44819efc55639a
SOPQLBY12A6310E992
5
['6c6289326f70321f2b3e072daa44819efc55639a', 'SOPREHY12AB018

## 最活跃的用户和最流行的歌曲

In [21]:
df_users_play_count = pd.read_csv(filepath_or_buffer= dpath + 'users_playcount.csv')
df_users_play_count.head(n =10)

play_count                                      user
0       13132  093cb74eb3c517c5179ae24caf0ebec51b24d2a2
1        9884  119b7c88d58d0c6eb051365c103da5caf817bea6
2        8210  3fa44653315697f42410a30cb766a4eb102080bb
3        7015  a2679496cd0af9779a92a13ff7c6af5c81ea8c7b
4        6494  d7d2d888ae04d16e994d6964214a1de81392ee04
5        6472  4ae01afa8f2430ea0704d502bc7b57fb52164882
6        6150  b7c24f770be6b802805ac0e2106624a517643c17
7        5656  113255a012b2affeab62607563d03fbdf31b08e7
8        5620  6d625c6557df84b60d90426c0116138b617b9449
9        5602  99ac3d883681e21ea68071019dba828ce76fe94d

In [23]:
df_songs_play_count = pd.read_csv(filepath_or_buffer= dpath + 'songs_playcount.csv')
df_songs_play_count.head(10)

play_count                song
0    12466637  SOSXLTC12AF72A7F54
1    11290840  SOWCKVR12A8C142411
2     9582939  SOUSMXX12AB0185C24
3     9350709  SONYKOW12AB01849C9
4     9053507  SOUVTSM12AC468F6A7
5     8535928  SOZVCRW12A67ADA0B7
6     7882419  SOXFPND12AB017C9D1
7     7875104  SOTWNDJ12A8C143984
8     7318597  SOPUCYA12A8C13A694
9     7317594  SOXWYZP12AF72A42A6

## 从总体数据中抽取子集
前800个用户
前5000个用户（共1百万用户）的播放次数和占总播放次数的40%（2/8原则：20%的用户播放了80%的次数）

In [27]:
N_SELECTED_USERS = 800
N_SELECTED_ITEMS = 800

df_users_play_count_subset = df_users_play_count.head(n=N_SELECTED_USERS)

n_total_play_count = sum(df_users_play_count.play_count)
slected_percent = (float(df_users_play_count_subset.play_count.sum())/n_total_play_count)*100

print(slected_percent)

1.37758555846


#取800个用户（万分之8的用户）首占总播放次数的1.4%

In [30]:
#共30万首歌曲
df_songs_play_count_subset = df_songs_play_count.head(n=N_SELECTED_ITEMS)

In [31]:
#前800个用户和800首歌曲
users_subset = list(df_users_play_count_subset.user)
songs_subset = list(df_songs_play_count_subset.song)

In [33]:
#如果机器内存不足，可参考前面逐条读txt文件
df_triplet_dataset = pd.read_csv(filepath_or_buffer = dpath + 'train_triplets.txt',sep='\t', 
                              header=None, names=['user','song','play_count'])
df_triplet_dataset_sub_users = df_triplet_dataset[df_triplet_dataset.user.isin(users_subset) ]
del(df_triplet_dataset)

df_triplet_dataset_sub_users_songs = df_triplet_dataset_sub_users[df_triplet_dataset_sub_users.song.isin(songs_subset)]
del(df_triplet_dataset_sub_users)

In [34]:
df_triplet_dataset_sub_users_songs.to_csv(path_or_buf = dpath + 'triplet_dataset_sub.csv', index=False)
df_triplet_dataset_sub_users_songs.shape

(37519, 3)

即使这样，还有4万条记录

In [36]:
df_triplet_dataset_sub_users_songs.head(n=10)

user                song  \
43812  4e11f45d732f4861772b2906f81a7d384552ad12  SOCKSGZ12A58A7CA4B   
43834  4e11f45d732f4861772b2906f81a7d384552ad12  SOCVTLJ12A6310F0FD   
43863  4e11f45d732f4861772b2906f81a7d384552ad12  SODLLYS12A8C13A96B   
43898  4e11f45d732f4861772b2906f81a7d384552ad12  SOEGIYH12A6D4FC0E3   
43961  4e11f45d732f4861772b2906f81a7d384552ad12  SOFRQTD12A81C233C0   
44044  4e11f45d732f4861772b2906f81a7d384552ad12  SOHEMBB12A6701E907   
44057  4e11f45d732f4861772b2906f81a7d384552ad12  SOHJOLH12A6310DFE5   
44131  4e11f45d732f4861772b2906f81a7d384552ad12  SOIZLKI12A6D4F7B61   
44146  4e11f45d732f4861772b2906f81a7d384552ad12  SOJGSIO12A8C141DBF   
44187  4e11f45d732f4861772b2906f81a7d384552ad12  SOKEYJQ12A6D4F6132   

       play_count  
43812           1  
43834           1  
43863           3  
43898           1  
43961           2  
44044           1  
44057           1  
44131           1  
44146           1  
44187           1